In [1]:
import zipfile
import numpy as np
import pandas
import os
from pprint import pprint
import json

In [ ]:
#zip_ref = zipfile.ZipFile('1927eve.zip', 'r')
#zip_ref.extractall('.')
#zip_ref.close()

#zip_ref = zipfile.ZipFile('1938eve.zip', 'r')
#zip_ref.extractall('.')
#zip_ref.close()


In [2]:
allfiles = []

teamarray = np.empty((0,4),dtype=object)

for line in open('TEAM1927').readlines():
    thisteam = []
    for x in line.split(','):
        thisteam.append(x)
    thisteam[-1] = thisteam[-1][0:-1]  # clear newline character at end
    teamarray = np.vstack((teamarray,thisteam))
#print(teamarray)
for oneyear in [1927,1938]:
    for oneteam in teamarray:
        filename = str(oneyear) + oneteam[0] + '.EV' + oneteam[1]
        allfiles.append(filename)
print(allfiles)

['1927BOS.EVA', '1927CHA.EVA', '1927CLE.EVA', '1927DET.EVA', '1927NYA.EVA', '1927PHA.EVA', '1927SLA.EVA', '1927WS1.EVA', '1927BRO.EVN', '1927BSN.EVN', '1927CHN.EVN', '1927CIN.EVN', '1927NY1.EVN', '1927PHI.EVN', '1927PIT.EVN', '1927SLN.EVN', '1938BOS.EVA', '1938CHA.EVA', '1938CLE.EVA', '1938DET.EVA', '1938NYA.EVA', '1938PHA.EVA', '1938SLA.EVA', '1938WS1.EVA', '1938BRO.EVN', '1938BSN.EVN', '1938CHN.EVN', '1938CIN.EVN', '1938NY1.EVN', '1938PHI.EVN', '1938PIT.EVN', '1938SLN.EVN']


In [3]:
allgames = []
gamecount = 0

for filename in allfiles:
    for line in open(filename).readlines():
        linearray = line.split(',')
        linearray[-1] = linearray[-1][0:-1]  # cut off newline character
    #    print(linearray[-1])
        if (linearray[0] == 'id'):
            # 'id' starts the next game, so immediately advance gamecount  

            # record prior game data by adding it to the gamelogs list, unless gamecount = -1
            if (gamecount > 0):
                thisgamedict['info'] = info_dict
                thisgamedict['visiting_starters'] = vis_start_list.tolist()
                thisgamedict['home_starters'] = home_start_list.tolist()

                # record game subs only if there were any subs
                if (len(vis_sub_list) > 0):
                    thisgamedict['visiting_subs'] = vis_sub_list.tolist()
                if (len(home_sub_list) > 0):
                    thisgamedict['home_subs'] = home_sub_list.tolist()

                thisgamedict['plays'] = plays.tolist()
                thisgamedict['data'] = data_list.tolist()
                # append the dictionary describing this game to the list of games
                allgames.append(thisgamedict)

            # advance the gamecount and initialize a new game
            gamecount = gamecount + 1
            thisgamedict = {}
            info_dict = {}
            start_dict = {}
            vis_start_list = np.empty((9,4),dtype=object)
            home_start_list = np.empty((9,4),dtype=object)
            vis_sub_list = np.empty((0,4),dtype=object)
            home_sub_list = np.empty((0,4),dtype=object)
            plays = np.empty((0,7),dtype=object)
            data_list = np.empty((0,2),dtype=object)
            batterscount = 0
            playnum = 0

            # the first thing to go into the new game is the game id.
            # the [0:-1] is there to cut off the newline character
            thisgamedict['id'] = linearray[1]

        if (linearray[0] == 'version'):
            thisgamedict['version'] = linearray[1]
        if (linearray[0] == 'info'):
            info_dict[linearray[1]] = linearray[2]
        if (linearray[0] == 'start'):
            batterscount = batterscount + 1
            if (linearray[3] == '0'):
                vis_start_list[batterscount-1,0] = linearray[1]
                vis_start_list[batterscount-1,1] = linearray[2]
                vis_start_list[batterscount-1,2] = linearray[4]
                vis_start_list[batterscount-1,3] = linearray[5]
            elif (linearray[3] == '1'):
                home_start_list[batterscount-10,0] = linearray[1]
                home_start_list[batterscount-10,1] = linearray[2]
                home_start_list[batterscount-10,2] = linearray[4]
                home_start_list[batterscount-10,3] = linearray[5]        
            else:
                print('NEITHER VISITOR NOR HOME????')

        if (linearray[0] == 'sub'):
            this_sub = []
            this_sub.append(linearray[1])
            this_sub.append(linearray[2])
            this_sub.append(linearray[4])
            this_sub.append(linearray[5])
            if (linearray[3] == '0'):
                vis_sub_list = np.vstack((vis_sub_list,this_sub))
            elif (linearray[3] == '1'):
                home_sub_list = np.vstack((home_sub_list,this_sub))
            else:
                print('NEITHER VISITOR NOR HOME????')

        if ((linearray[0] == 'play') | (linearray[0] == 'com')):
    #        print(linearray)
            thisplay = []
            thisplay.append(playnum)
            if (linearray[0] == 'play'):
                for i in range(1,7):
                    thisplay.append(linearray[i])
            else:   # if it's a comment, record the comment text as a string in place of the play text
                comment_string = ''
                for i in range(1,len(linearray)):
                    comment_string += str(linearray[i])
                for i in range(1,6):
                    thisplay.append('')
                thisplay.append(comment_string)
            plays = np.vstack((plays,thisplay))
            playnum = playnum + 1

        if (linearray[0] == 'data'):
            thisdata = np.empty((2),dtype=object)
            thisdata[0] = linearray[2]
            thisdata[1] = linearray[3]
            data_list = np.vstack((data_list,thisdata))
#    if ((linearray[0] != 'id') & (linearray[0] != 'version') & (linearray[0] != 'info') & (linearray[0] != 'start') & (linearray[0] != 'sub') & (linearray[0] != 'play') & (linearray[0] != 'data')):
#        print(linearray)

#for i in range(0,len(gamelogs)):
#    print('i = ',i)
#    pprint(allevents[i])
#    print('\n')
print('ahoy')
#print(allgames[0])

ahoy


In [17]:
nEvents = 0
for game in allgames:
    nEvents = nEvents + len(game['plays'])
print(nEvents)
events = np.empty((nEvents,3),dtype=object)
eventno = 0
for game in allgames:
    for j in range(0,len(game['plays'])):
        events[eventno,0] = game['id']
        events[eventno,1] = game['info']['visteam']
        events[eventno,2] = game['info']['hometeam']
        eventno = eventno + 1
events

159873


array([['BOS192704230', 'WS1', 'BOS'],
       ['BOS192704230', 'WS1', 'BOS'],
       ['BOS192704230', 'WS1', 'BOS'],
       ..., 
       ['SLN193810011', 'CHN', 'SLN'],
       ['SLN193810011', 'CHN', 'SLN'],
       ['SLN193810011', 'CHN', 'SLN']], dtype=object)

In [4]:
with open('0events.json', 'w') as f:
    json.dump(allgames, f)
print('ok')

ok


In [5]:
with open('0events.json','r') as f:
    thingy = json.load(f)
thingy

[{'data': [['crowg102', '4'],
   ['liseh101', '0'],
   ['braxg101', '1'],
   ['marbf101', '0'],
   ['harrs101', '3']],
  'home_starters': [['wannp101', '"Pee-Wee Wanninger"', '1', '6'],
   ['rothj101', '"Jack Rothrock"', '2', '4'],
   ['tobij101', '"Jack Tobin"', '3', '9'],
   ['flagi101', '"Ira Flagstead"', '4', '8'],
   ['jacow101', '"William Jacobson"', '5', '7'],
   ['todtp101', '"Phil Todt"', '6', '3'],
   ['hanef101', '"Fred Haney"', '7', '5'],
   ['hofmf101', '"Fred Hofmann"', '8', '2'],
   ['harrs101', '"Slim Harriss"', '9', '1']],
  'id': 'BOS192704230',
  'info': {'attendance': '5000',
   'date': '1927/04/23',
   'daynight': 'day',
   'fieldcond': 'unknown',
   'gwrbi': '',
   'hometeam': 'BOS',
   'howscored': 'park',
   'inputprogvers': '"version 7RS(19) of 07/07/92"',
   'inputter': '"Comly"',
   'inputtime': '2011/09/10 11:14AM',
   'lp': 'crowg102',
   'number': '0',
   'pitches': 'none',
   'precip': 'unknown',
   'save': '',
   'scorer': '"115"',
   'site': 'BOS07',
  